While zero-shot learning models like BERT, BART, or Gemini can make predictions without prior training on specific tasks, we still need test data to evaluate their performance. This test data provides us with ground truth labels so we can compare the model’s predictions to actual labels and calculate metrics like F1-score, precision, recall, and accuracy.

Zero-shot means the model hasn’t been fine-tuned on this dataset, but it still needs input text (test data) to classify, and we need actual labels to verify the correctness of its predictions.

Loading the dataset helps us measure how well the model performs on real-world data in a zero-shot scenario by comparing predicted vs. true labels.

In summary, we use the dataset in zero-shot experiments to evaluate how the model performs on unseen tasks, which is critical for drawing conclusions about its zero-shot learning capabilities.

zeroshot with gemini

In [2]:
import pandas as pd
import torch
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from sklearn.metrics import classification_report, f1_score, accuracy_score, precision_score, recall_score
from torch.utils.data import DataLoader, Dataset

# Load your dataset
df = pd.read_csv('labeled_comments_cleaned.csv')
df.fillna('', inplace=True)

# Define the category names for each level
level_categories = {
    'level_0': ['INFORMATION EXCHANGE', 'MODIFICATION', 'SOCIAL COMMUNICATION', 'OTHER'],
    'level_1': ['REQUESTED', 'EXECUTION', 'DISCUSSION', 'PROVIDED', 'FEEDBACK', 'ACKNOWLEDGMENT'],
    'level_2': ['REQUESTING_CONFIRMATION', 'PROMISE', 'CONTENT', 'REFERENCE', 'CONTEXT', 'THREAD', 'DONE', 'FORMAT', 'ASKING_DETAILS'],
    'level_3': ['POTENTIAL_CHANGE', 'NOT_POTENTIAL_CHANGE', 'EXPLICIT', 'NOT_EXPLICIT'],
    'level_4': ['CHANGE', 'ADD', 'DELETE']
}

# Switch to GPU if available
device = 'cuda' if torch.cuda.is_available() else 'cpu'

# Load pre-trained model and tokenizer
tokenizer = AutoTokenizer.from_pretrained('google/gemma-2b')
model = AutoModelForSequenceClassification.from_pretrained('google/gemma-2b').to(device).half()

# Dataset class for DataLoader
class CommentsDataset(Dataset):
    def __init__(self, comments, labels):
        self.comments = comments
        self.labels = labels

    def __len__(self):
        return len(self.comments)

    def __getitem__(self, idx):
        return self.comments[idx], self.labels[idx]

# Function to predict labels for each batch of comments
def predict_labels_batch(comments, candidate_labels):
    inputs = tokenizer(comments, return_tensors="pt", padding=True, truncation=True, max_length=128).to(device)
    with torch.no_grad():
        outputs = model(**inputs)
    logits = outputs.logits
    predicted_label_ids = torch.argmax(logits, dim=1).tolist()  # Get the highest scoring label IDs
    predicted_labels = [candidate_labels[label_id] if label_id < len(candidate_labels) else "Unknown" for label_id in predicted_label_ids]
    return predicted_labels

# Function to evaluate
def evaluate_for_level(level_name, candidate_labels):
    print(f"\nEvaluating for {level_name}...")
    X_test = df['comment_full_text']  # Comments for classification
    y_test = df[level_name].tolist()  # Ground truth labels for this level
    X_test, y_test = zip(*[(comment, label) for comment, label in zip(X_test, y_test) if label])

    # Use DataLoader for better performance
    dataset = CommentsDataset(X_test, y_test)
    test_loader = DataLoader(dataset, batch_size=64, shuffle=False, num_workers=4)

    predicted_labels = []
    for batch in test_loader:
        batch_comments, _ = batch
        predicted_labels.extend(predict_labels_batch(batch_comments, candidate_labels))

    y_test = [label.lower() for label in y_test]
    predicted_labels = [label.lower() for label in predicted_labels]

    filtered_actual = [label for i, label in enumerate(y_test) if predicted_labels[i] != "unknown"]
    filtered_predicted = [label for label in predicted_labels if label != "unknown"]

    print("Calculating metrics...")
    f1 = f1_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    precision = precision_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    recall = recall_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    accuracy = accuracy_score(filtered_actual, filtered_predicted)
    report = classification_report(filtered_actual, filtered_predicted, zero_division=1)

    print(f"F1 Score for {level_name}: {f1}")
    print(f"Precision for {level_name}: {precision}")
    print(f"Recall for {level_name}: {recall}")
    print(f"Accuracy for {level_name}: {accuracy}")
    print(f"Classification Report for {level_name}:\n", report)

# Evaluate for all levels
for level_name, candidate_labels in level_categories.items():
    evaluate_for_level(level_name, candidate_labels)


`config.hidden_act` is ignored, you should use `config.hidden_activation` instead.
Gemma's activation function will be set to `gelu_pytorch_tanh`. Please, use
`config.hidden_activation` if you want to override this behaviour.
See https://github.com/huggingface/transformers/pull/29402 for more details.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Some weights of GemmaForSequenceClassification were not initialized from the model checkpoint at google/gemma-2b and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



Evaluating for level_0...
Calculating metrics...
F1 Score for level_0: 0.41254153542953753
Precision for level_0: 0.5546774938328606
Recall for level_0: 0.4510118212783009
Accuracy for level_0: 0.4510118212783009
Classification Report for level_0:
                       precision    recall  f1-score   support

information exchange       0.56      0.36      0.44      2483
        modification       0.40      0.72      0.51      1886
               other       1.00      0.00      0.00       273
social communication       1.00      0.00      0.00       349

            accuracy                           0.45      4991
           macro avg       0.74      0.27      0.24      4991
        weighted avg       0.55      0.45      0.41      4991


Evaluating for level_1...


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

...

Calculating metrics...
F1 Score for level_2: 0.0024410397421714162
Precision for level_2: 0.9667885214172521
Recall for level_2: 0.01471529110684581
Accuracy for level_2: 0.01471529110684581
Classification Report for level_2:
                          precision    recall  f1-score   support

         asking_details       1.00      0.00      0.00       553
                content       1.00      0.00      0.00      1384
                context       1.00      0.00      0.00      1425
                   done       1.00      0.00      0.00       253
                 format       1.00      0.00      0.00       405
                promise       0.00      0.24      0.00        17
              reference       1.00      0.00      0.00       358
requesting_confirmation       0.04      0.45      0.08       145
                 thread       1.00      0.00      0.00       149

               accuracy                           0.01      4689
              macro avg       0.78      0.08      0.01  

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Calculating metrics...
F1 Score for level_3: 0.25626044427067196
Precision for level_3: 0.6134491811508861
Recall for level_3: 0.31657608695652173
Accuracy for level_3: 0.31657608695652173
Classification Report for level_3:
                       precision    recall  f1-score   support

            explicit       1.00      0.00      0.00      1504
        not_explicit       1.00      0.00      0.00        83
not_potential_change       0.24      0.71      0.35       977
    potential_change       0.48      0.38      0.42      1852

            accuracy                           0.32      4416
           macro avg       0.68      0.27      0.19      4416
        weighted avg       0.61      0.32      0.26      4416


Evaluating for level_4...


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Calculating metrics...
F1 Score for level_4: 0.4317266612236479
Precision for level_4: 0.5213071221108501
Recall for level_4: 0.4738583719391132
Accuracy for level_4: 0.4738583719391132
Classification Report for level_4:
               precision    recall  f1-score   support

         add       0.51      0.69      0.59       787
      change       0.39      0.31      0.35       551
      delete       1.00      0.00      0.00       173

    accuracy                           0.47      1511
   macro avg       0.63      0.33      0.31      1511
weighted avg       0.52      0.47      0.43      1511



Zero-shot Evaluation using the Gemini Model:

Dataset Preparation: I loaded the labeled_comments_cleaned.csv dataset, which contains hierarchical labels (from level_0 to level_4) for comments. I then selected the comment text (X_test) and corresponding labels (y_test) for each level to evaluate.

Model Setup: I used the pre-trained Gemini model (google/gemma-2b) for zero-shot classification. This model wasn't fine-tuned on my specific dataset, so I used AutoTokenizer and AutoModelForSequenceClassification to prepare it for inference.

Zero-shot Prediction: For each hierarchical level (level_0 to level_4), I predicted the category labels for the comments using the Gemini model. I then compared the predicted labels with the actual labels from the dataset.

Metrics Calculation: I calculated F1 Score, Precision, Recall, and Accuracy for each hierarchical level. The model's performance was relatively low across most levels, particularly in level_1, level_2, and level_3, as the model had not been fine-tuned for this specific task.

Outcome: The Gemini model was evaluated in a zero-shot setting, meaning it was used without task-specific fine-tuning. The results showed that while the model can predict labels, its performance (e.g., F1 score, recall) was limited. The model would likely perform better with task-specific training or fine-tuning.

zero shot with bert 

In [5]:
import torch
import pandas as pd
from transformers import BertTokenizer, BertForSequenceClassification
from sklearn.metrics import classification_report, f1_score, accuracy_score, precision_score, recall_score

# Load your dataset
df = pd.read_csv('labeled_comments_cleaned.csv')

# Fill missing values with empty strings
df.fillna('', inplace=True)

# Define the category names for all levels
level_categories = {
    'level_0': ['INFORMATION EXCHANGE', 'MODIFICATION', 'SOCIAL COMMUNICATION', 'OTHER'],
    'level_1': ['REQUESTED', 'EXECUTION', 'DISCUSSION', 'PROVIDED', 'FEEDBACK', 'ACKNOWLEDGMENT'],
    'level_2': ['REQUESTING_CONFIRMATION', 'PROMISE', 'CONTENT', 'REFERENCE', 'CONTEXT', 'THREAD', 'DONE', 'FORMAT', 'ASKING_DETAILS'],
    'level_3': ['POTENTIAL_CHANGE', 'NOT_POTENTIAL_CHANGE', 'EXPLICIT', 'NOT_EXPLICIT'],
    'level_4': ['CHANGE', 'ADD', 'DELETE']
}

# Initialize the pre-trained BERT model and tokenizer (for zero-shot)
device = 'cuda' if torch.cuda.is_available() else 'cpu'
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')  # Pre-trained BERT model
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=max(len(categories) for categories in level_categories.values())).to(device)

# Function to predict labels for each batch of comments using the pre-trained BERT model
def predict_labels_batch(comments, candidate_labels):
    inputs = tokenizer(comments, return_tensors="pt", padding=True, truncation=True, max_length=128).to(device)
    with torch.no_grad():
        outputs = model(**inputs)
    logits = outputs.logits
    predicted_label_ids = torch.argmax(logits, dim=1).tolist()  # Get the highest scoring label IDs
    predicted_labels = [candidate_labels[label_id] if label_id < len(candidate_labels) else "Unknown" for label_id in predicted_label_ids]
    return predicted_labels

# Evaluate for a specific level
def evaluate_for_level(level_name, candidate_labels):
    print(f"\nEvaluating for {level_name}...")

    # Use the appropriate level labels
    X_test = df['comment_full_text']  # Comments for classification
    y_test = df[level_name].tolist()  # Ground truth labels for this level

    # Remove empty labels for this level
    X_test, y_test = zip(*[(comment, label) for comment, label in zip(X_test, y_test) if label])

    # Run predictions on all test comments (in batches)
    batch_size = 32  # You can adjust this based on memory constraints
    predicted_labels = []
    for i in range(0, len(X_test), batch_size):
        batch_comments = X_test[i:i+batch_size]
        predicted_labels.extend(predict_labels_batch(batch_comments, candidate_labels))
        print(f"Processed {i+len(batch_comments)}/{len(X_test)} comments.")

    # Normalize both actual and predicted labels to lowercase for comparison
    y_test = [label.lower() for label in y_test]
    predicted_labels = [label.lower() for label in predicted_labels]

    # Remove "Unknown" labels from predicted labels and corresponding actual labels
    filtered_actual = [label for i, label in enumerate(y_test) if predicted_labels[i] != "unknown"]
    filtered_predicted = [label for label in predicted_labels if label != "unknown"]

    # Calculate metrics for zero-shot classification
    print("Calculating metrics...")

    # Calculate F1 Score, Precision, Recall, and Accuracy
    f1 = f1_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    precision = precision_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    recall = recall_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    accuracy = accuracy_score(filtered_actual, filtered_predicted)

    # Print the classification report for detailed metrics
    report = classification_report(filtered_actual, filtered_predicted, zero_division=1)

    # Output the metrics
    print(f"F1 Score for {level_name}: {f1}")
    print(f"Precision for {level_name}: {precision}")
    print(f"Recall for {level_name}: {recall}")
    print(f"Accuracy for {level_name}: {accuracy}")
    print(f"Classification Report for {level_name}:\n", report)

# Evaluate for all levels (from level_0 to level_4)
for level_name, candidate_labels in level_categories.items():
    evaluate_for_level(level_name, candidate_labels)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.



Evaluating for level_0...
Processed 32/4991 comments.
Processed 64/4991 comments.
Processed 96/4991 comments.
Processed 128/4991 comments.
Processed 160/4991 comments.
Processed 192/4991 comments.
Processed 224/4991 comments.
Processed 256/4991 comments.
Processed 288/4991 comments.
Processed 320/4991 comments.
Processed 352/4991 comments.
Processed 384/4991 comments.
Processed 416/4991 comments.
Processed 448/4991 comments.
Processed 480/4991 comments.
Processed 512/4991 comments.
Processed 544/4991 comments.
Processed 576/4991 comments.
Processed 608/4991 comments.
Processed 640/4991 comments.
Processed 672/4991 comments.
Processed 704/4991 comments.
Processed 736/4991 comments.
Processed 768/4991 comments.
Processed 800/4991 comments.
Processed 832/4991 comments.
Processed 864/4991 comments.
Processed 896/4991 comments.
Processed 928/4991 comments.
Processed 960/4991 comments.
Processed 992/4991 comments.
Processed 1024/4991 comments.
Processed 1056/4991 comments.
Processed 1088/49

Explanation:
Dataset: We load the dataset labeled_comments_cleaned.csv and prepare it by handling missing values.
Model and Tokenizer: We load a pre-trained BERT model (bert-base-uncased) and a tokenizer. The model is specified with the number of output labels as the maximum number of categories across all hierarchical levels.
Prediction Function: predict_labels_batch() makes predictions for each batch of comments and converts logits into the highest-scoring label.
Evaluation: For each hierarchical level (level_0 to level_4), the script:
Runs the comments through the BERT model to get predictions.
Calculates F1 score, Precision, Recall, and Accuracy.
Prints a detailed classification report for each level.

Zero shot with bart

In [10]:
import torch
import pandas as pd
from transformers import BartTokenizer, BartForSequenceClassification
from sklearn.metrics import classification_report, f1_score, accuracy_score, precision_score, recall_score

# Load your dataset
df = pd.read_csv('labeled_comments_cleaned.csv')

# Fill missing values with empty strings
df.fillna('', inplace=True)

# Define the category names for all levels
level_categories = {
    'level_0': ['INFORMATION EXCHANGE', 'MODIFICATION', 'SOCIAL COMMUNICATION', 'OTHER'],
    'level_1': ['REQUESTED', 'EXECUTION', 'DISCUSSION', 'PROVIDED', 'FEEDBACK', 'ACKNOWLEDGMENT'],
    'level_2': ['REQUESTING_CONFIRMATION', 'PROMISE', 'CONTENT', 'REFERENCE', 'CONTEXT', 'THREAD', 'DONE', 'FORMAT', 'ASKING_DETAILS'],
    'level_3': ['POTENTIAL_CHANGE', 'NOT_POTENTIAL_CHANGE', 'EXPLICIT', 'NOT_EXPLICIT'],
    'level_4': ['CHANGE', 'ADD', 'DELETE']
}

# Initialize the pre-trained BART model and tokenizer (for zero-shot)
device = 'cuda' if torch.cuda.is_available() else 'cpu'
tokenizer = BartTokenizer.from_pretrained('facebook/bart-large-mnli')  # Pre-trained BART model for zero-shot
model = BartForSequenceClassification.from_pretrained('facebook/bart-large-mnli').to(device)

# Function to predict labels for each comment using the pre-trained BART model
def predict_label_for_comment(comment, candidate_labels):
    # For zero-shot classification, we test the comment against each candidate label
    inputs = tokenizer([f"This example is about {label}." for label in candidate_labels],
                       [comment] * len(candidate_labels),  # Pair the comment with each label
                       return_tensors="pt",
                       padding=True,
                       truncation=True,
                       max_length=128)
    
    inputs = {key: val.to(device) for key, val in inputs.items()}  # Move inputs to GPU if available
    
    with torch.no_grad():
        outputs = model(**inputs)
    
    logits = outputs.logits
    predicted_label_id = torch.argmax(logits[:, 0]).item()  # Get the highest scoring label ID for the first logit
    predicted_label = candidate_labels[predicted_label_id]
    return predicted_label

# Evaluate for a specific level
def evaluate_for_level(level_name, candidate_labels):
    print(f"\nEvaluating for {level_name}...")

    # Use the appropriate level labels
    X_test = df['comment_full_text']  # Comments for classification
    y_test = df[level_name].tolist()  # Ground truth labels for this level

    # Remove empty labels for this level
    X_test, y_test = zip(*[(comment, label) for comment, label in zip(X_test, y_test) if label])

    # Run predictions on all test comments (sequentially for now)
    predicted_labels = []
    for i, comment in enumerate(X_test):
        predicted_label = predict_label_for_comment(comment, candidate_labels)
        predicted_labels.append(predicted_label)
        if (i + 1) % 32 == 0:
            print(f"Processed {i + 1}/{len(X_test)} comments.")
    
    # Normalize both actual and predicted labels to lowercase for comparison
    y_test = [label.lower() for label in y_test]
    predicted_labels = [label.lower() for label in predicted_labels]

    # Remove "Unknown" labels from predicted labels and corresponding actual labels
    filtered_actual = [label for i, label in enumerate(y_test) if predicted_labels[i] != "unknown"]
    filtered_predicted = [label for label in predicted_labels if label != "unknown"]

    # Calculate metrics for zero-shot classification
    print("Calculating metrics...")

    # Calculate F1 Score, Precision, Recall, and Accuracy
    f1 = f1_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    precision = precision_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    recall = recall_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    accuracy = accuracy_score(filtered_actual, filtered_predicted)

    # Print the classification report for detailed metrics
    report = classification_report(filtered_actual, filtered_predicted, zero_division=1)

    # Output the metrics
    print(f"F1 Score for {level_name}: {f1}")
    print(f"Precision for {level_name}: {precision}")
    print(f"Recall for {level_name}: {recall}")
    print(f"Accuracy for {level_name}: {accuracy}")
    print(f"Classification Report for {level_name}:\n", report)

# Evaluate for all levels (from level_0 to level_4)
for level_name, candidate_labels in level_categories.items():
    evaluate_for_level(level_name, candidate_labels)



Evaluating for level_0...


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


Processed 32/4991 comments.


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Processed 64/4991 comments.
Processed 96/4991 comments.
Processed 128/4991 comments.


...

Processed 1440/1511 comments.


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Processed 1472/1511 comments.


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Processed 1504/1511 comments.
Calculating metrics...
F1 Score for level_4: 0.3581692611970854
Precision for level_4: 0.3985337913972372
Recall for level_4: 0.32892124420913305
Accuracy for level_4: 0.32892124420913305
Classification Report for level_4:
               precision    recall  f1-score   support

         add       0.51      0.43      0.47       787
      change       0.36      0.26      0.30       551
      delete       0.03      0.08      0.05       173

    accuracy                           0.33      1511
   macro avg       0.30      0.26      0.27      1511
weighted avg       0.40      0.33      0.36      1511



Explanation:
BART Model: We use facebook/bart-large-mnli because it is specifically fine-tuned for zero-shot classification tasks. It can infer if a given text "entails" a candidate label or not, making it ideal for this task.
Candidate Labels: These are the possible categories for each level (e.g., for level_0, it's "Information Exchange," "Modification," etc.).
Prediction Logic: For each comment, we run it through the model along with the candidate labels. BART predicts which label the comment is most likely related to by computing the entailment score.
Metrics: After predicting, we compare the results with ground truth labels and calculate metrics (F1, Precision, Recall, Accuracy) to evaluate performance.
Why Use BART for Zero-shot?
BART's facebook/bart-large-mnli is one of the state-of-the-art models specifically designed for zero-shot tasks. Unlike BERT, which requires fine-tuning for classification, BART has been pre-trained to perform tasks such as recognizing if a sentence entails, contradicts, or is neutral to another sentence (which we leverage for zero-shot classification).

This approach will allow you to perform zero-shot classification for each hierarchical level and evaluate BART's performance across multiple categories!







Zero -shot with roberta model

In [11]:
import torch
import pandas as pd
from transformers import RobertaTokenizer, RobertaForSequenceClassification
from sklearn.metrics import classification_report, f1_score, accuracy_score, precision_score, recall_score

# Load your dataset
df = pd.read_csv('labeled_comments_cleaned.csv')

# Fill missing values with empty strings
df.fillna('', inplace=True)

# Define the category names for all levels
level_categories = {
    'level_0': ['INFORMATION EXCHANGE', 'MODIFICATION', 'SOCIAL COMMUNICATION', 'OTHER'],
    'level_1': ['REQUESTED', 'EXECUTION', 'DISCUSSION', 'PROVIDED', 'FEEDBACK', 'ACKNOWLEDGMENT'],
    'level_2': ['REQUESTING_CONFIRMATION', 'PROMISE', 'CONTENT', 'REFERENCE', 'CONTEXT', 'THREAD', 'DONE', 'FORMAT', 'ASKING_DETAILS'],
    'level_3': ['POTENTIAL_CHANGE', 'NOT_POTENTIAL_CHANGE', 'EXPLICIT', 'NOT_EXPLICIT'],
    'level_4': ['CHANGE', 'ADD', 'DELETE']
}

# Initialize the pre-trained RoBERTa model and tokenizer (for zero-shot)
device = 'cuda' if torch.cuda.is_available() else 'cpu'
tokenizer = RobertaTokenizer.from_pretrained('roberta-large-mnli')  # Pre-trained RoBERTa model for NLI tasks
model = RobertaForSequenceClassification.from_pretrained('roberta-large-mnli').to(device)

# Function to predict labels for each comment using the pre-trained RoBERTa model
def predict_label_for_comment(comment, candidate_labels):
    # For zero-shot classification, we test the comment against each candidate label
    inputs = tokenizer([f"This example is about {label}." for label in candidate_labels],
                       [comment] * len(candidate_labels),  # Pair the comment with each label
                       return_tensors="pt",
                       padding=True,
                       truncation=True,
                       max_length=128)
    
    inputs = {key: val.to(device) for key, val in inputs.items()}  # Move inputs to GPU if available
    
    with torch.no_grad():
        outputs = model(**inputs)
    
    logits = outputs.logits
    predicted_label_id = torch.argmax(logits[:, 0]).item()  # Get the highest scoring label ID for the first logit
    predicted_label = candidate_labels[predicted_label_id]
    return predicted_label

# Evaluate for a specific level
def evaluate_for_level(level_name, candidate_labels):
    print(f"\nEvaluating for {level_name}...")

    # Use the appropriate level labels
    X_test = df['comment_full_text']  # Comments for classification
    y_test = df[level_name].tolist()  # Ground truth labels for this level

    # Remove empty labels for this level
    X_test, y_test = zip(*[(comment, label) for comment, label in zip(X_test, y_test) if label])

    # Run predictions on all test comments (sequentially for now)
    predicted_labels = []
    for i, comment in enumerate(X_test):
        predicted_label = predict_label_for_comment(comment, candidate_labels)
        predicted_labels.append(predicted_label)
        if (i + 1) % 32 == 0:
            print(f"Processed {i + 1}/{len(X_test)} comments.")
    
    # Normalize both actual and predicted labels to lowercase for comparison
    y_test = [label.lower() for label in y_test]
    predicted_labels = [label.lower() for label in predicted_labels]

    # Remove "Unknown" labels from predicted labels and corresponding actual labels
    filtered_actual = [label for i, label in enumerate(y_test) if predicted_labels[i] != "unknown"]
    filtered_predicted = [label for label in predicted_labels if label != "unknown"]

    # Calculate metrics for zero-shot classification
    print("Calculating metrics...")

    # Calculate F1 Score, Precision, Recall, and Accuracy
    f1 = f1_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    precision = precision_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    recall = recall_score(filtered_actual, filtered_predicted, average='weighted', zero_division=1)
    accuracy = accuracy_score(filtered_actual, filtered_predicted)

    # Print the classification report for detailed metrics
    report = classification_report(filtered_actual, filtered_predicted, zero_division=1)

    # Output the metrics
    print(f"F1 Score for {level_name}: {f1}")
    print(f"Precision for {level_name}: {precision}")
    print(f"Recall for {level_name}: {recall}")
    print(f"Accuracy for {level_name}: {accuracy}")
    print(f"Classification Report for {level_name}:\n", report)

# Evaluate for all levels (from level_0 to level_4)
for level_name, candidate_labels in level_categories.items():
    evaluate_for_level(level_name, candidate_labels)


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

/home/spati/.local/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


...

Processed 1440/1511 comments.


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Processed 1472/1511 comments.


Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pai

Processed 1504/1511 comments.
Calculating metrics...
F1 Score for level_4: 0.28664941044836484
Precision for level_4: 0.36470976592886617
Recall for level_4: 0.24222369291859697
Accuracy for level_4: 0.24222369291859697
Classification Report for level_4:
               precision    recall  f1-score   support

         add       0.44      0.27      0.33       787
      change       0.36      0.26      0.30       551
      delete       0.02      0.09      0.04       173

    accuracy                           0.24      1511
   macro avg       0.28      0.20      0.22      1511
weighted avg       0.36      0.24      0.29      1511



Explanation:
RoBERTa Model (roberta-large-mnli): We are using the RoBERTa model fine-tuned for Natural Language Inference (NLI) with facebook/roberta-large-mnli. This model can classify text pairs, which we can repurpose for zero-shot classification by framing each candidate label as a hypothesis and the comment as the premise.

Hypothesis-Premise Format: For each comment, we generate multiple hypotheses using each candidate label. For example, if a candidate label is "Information Exchange," the hypothesis would be "This example is about Information Exchange." The model scores each hypothesis, and the label with the highest score is selected as the predicted label.

Processing Batches: The code loops over each comment, predicting a label for each one by comparing it with each candidate label. Predictions are made using torch.argmax(logits[:, 0]), which extracts the label with the highest score.

Metrics: After prediction, the f1_score, precision_score, recall_score, and accuracy_score are calculated for each level. A detailed classification report is also printed.

zero shit with hcpas

retrain hcaps net

Hierarchical Attention Network (HAN) with BiLSTM:
Why HAN?
It directly addresses hierarchical structures by applying attention mechanisms at both the word level (within a sentence) and the sentence level (within a document).
It is a competitive alternative to transformer-based models for hierarchical tasks, and will allow us to directly compare results with BERT, BART, RoBERTa, and Gemini.

In [55]:
import torch
import torch.nn as nn
import pandas as pd
import numpy as np
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.model_selection import train_test_split
from torch.utils.data import DataLoader, Dataset
from sklearn.metrics import f1_score, classification_report
from torch.optim.lr_scheduler import OneCycleLR

# Step 1: Load Pre-trained GloVe embeddings
def load_glove_embeddings(glove_file, embedding_dim=300):
    embeddings_index = {}
    with open(glove_file, 'r', encoding='utf-8') as f:
        for line in f:
            values = line.split()
            word = values[0]
            coefs = np.asarray(values[1:], dtype='float32')
            embeddings_index[word] = coefs
    print(f'Loaded {len(embeddings_index)} word vectors.')
    return embeddings_index

# Load the GloVe embeddings
embedding_dim = 300
glove_file = 'glove.6B.300d.txt'
glove_embeddings = load_glove_embeddings(glove_file, embedding_dim)

# Step 2: Data Preparation
df = pd.read_csv('labeled_comments_cleaned.csv')
df.fillna('', inplace=True)

# Combine all label columns into a list of labels per row
df['combined_labels'] = df[['level_0', 'level_1', 'level_2', 'level_3', 'level_4']].values.tolist()

# MultiLabelBinarizer for one-hot encoding the labels
mlb = MultiLabelBinarizer()
y = mlb.fit_transform(df['combined_labels'])

# Selecting the feature variable
X = df['comment_full_text']

# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Step 3: Dataset Class
class CommentsDataset(Dataset):
    def __init__(self, texts, labels, glove_embeddings, embedding_dim=300, max_len=128):
        self.texts = texts.reset_index(drop=True)
        self.labels = labels
        self.glove_embeddings = glove_embeddings
        self.embedding_dim = embedding_dim
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        tokenized_text = text.split()[:self.max_len]
        
        # Convert words to GloVe embeddings, pad with zeros if shorter than max_len
        embedding_matrix = np.zeros((self.max_len, self.embedding_dim))
        for i, word in enumerate(tokenized_text):
            embedding_matrix[i] = self.glove_embeddings.get(word, np.zeros(self.embedding_dim))
        
        input_tensor = torch.tensor(embedding_matrix, dtype=torch.float32)
        label_tensor = torch.tensor(label, dtype=torch.float32)
        return input_tensor, label_tensor

# Step 4: Create dataset and dataloaders
train_dataset = CommentsDataset(X_train, y_train, glove_embeddings, embedding_dim=embedding_dim)
test_dataset = CommentsDataset(X_test, y_test, glove_embeddings, embedding_dim=embedding_dim)

train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64)

# Step 5: Define HAN with BiGRU Model, Layer Norm, and Gradient Clipping
class AttentionLayer(nn.Module):
    def __init__(self, hidden_size):
        super(AttentionLayer, self).__init__()
        self.attention = nn.Linear(hidden_size, 1)

    def forward(self, inputs):
        scores = self.attention(inputs).squeeze(-1)
        attention_weights = torch.softmax(scores, dim=1)
        context_vector = torch.sum(attention_weights.unsqueeze(-1) * inputs, dim=1)
        return context_vector, attention_weights

class HierarchicalAttentionNetwork(nn.Module):
    def __init__(self, hidden_size, num_labels=27, dropout_prob=0.5):
        super(HierarchicalAttentionNetwork, self).__init__()
        self.bigru_word = nn.GRU(embedding_dim, hidden_size, batch_first=True, bidirectional=True)
        self.layer_norm_word = nn.LayerNorm(hidden_size * 2)  # Added LayerNorm
        self.bigru_sentence = nn.GRU(hidden_size * 2, hidden_size, batch_first=True, bidirectional=True)
        self.layer_norm_sentence = nn.LayerNorm(hidden_size * 2)  # Added LayerNorm
        self.word_attention = AttentionLayer(hidden_size * 2)
        self.sentence_attention = AttentionLayer(hidden_size * 2)
        self.fc = nn.Linear(hidden_size * 2, num_labels)  # 27 labels across all levels
        self.dropout = nn.Dropout(dropout_prob)

    def forward(self, inputs):
        word_level_output, _ = self.bigru_word(inputs)
        word_level_output = self.layer_norm_word(word_level_output)
        word_context, word_attention_weights = self.word_attention(word_level_output)
        sentence_level_output, _ = self.bigru_sentence(word_context.unsqueeze(1))
        sentence_level_output = self.layer_norm_sentence(sentence_level_output)
        sentence_context, sentence_attention_weights = self.sentence_attention(sentence_level_output)
        sentence_context = self.dropout(sentence_context)
        logits = self.fc(sentence_context)
        return logits

# Step 6: Initialize Model, Optimizer, and Loss Function
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = HierarchicalAttentionNetwork(hidden_size=256, num_labels=27).to(device)  # Changed to 27 labels

optimizer = torch.optim.AdamW(model.parameters(), lr=1e-4, weight_decay=1e-5)
scheduler = OneCycleLR(optimizer, max_lr=1e-3, steps_per_epoch=len(train_loader), epochs=30)
criterion = nn.BCEWithLogitsLoss()

# Step 7: Training Loop with Gradient Clipping
def train_epoch(model, dataloader, optimizer, criterion, device, clip_value=1.0):
    model.train()
    total_loss = 0
    for inputs, labels in dataloader:
        inputs, labels = inputs.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        # Gradient clipping
        nn.utils.clip_grad_norm_(model.parameters(), clip_value)
        optimizer.step()
        total_loss += loss.item()
    return total_loss / len(dataloader)

# Step 8: Evaluation Loop
def eval_model(model, dataloader, criterion, device):
    model.eval()
    total_loss = 0
    preds, true_labels = [], []
    with torch.no_grad():
        for inputs, labels in dataloader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            total_loss += loss.item()
            preds.append(torch.sigmoid(outputs).cpu().numpy())
            true_labels.append(labels.cpu().numpy())
    
    preds = np.vstack(preds)
    true_labels = np.vstack(true_labels)
    
    return total_loss / len(dataloader), preds, true_labels

# Step 9: Run Training and Evaluation with Early Stopping
best_val_loss = float('inf')
patience = 3
epochs_no_improve = 0
n_epochs = 30

for epoch in range(n_epochs):
    train_loss = train_epoch(model, train_loader, optimizer, criterion, device)
    val_loss, val_preds, val_labels = eval_model(model, test_loader, criterion, device)
    
    scheduler.step()

    val_preds = (val_preds > 0.5).astype(int)
    f1 = f1_score(val_labels, val_preds, average='weighted')
    
    print(f"Epoch {epoch + 1}, Train Loss: {train_loss:.4f}, Val Loss: {val_loss:.4f}, Val F1 Score: {f1:.4f}")

    if val_loss < best_val_loss:
        best_val_loss = val_loss
        epochs_no_improve = 0
        torch.save(model.state_dict(), 'best_han_bigru_model.pth')
    else:
        epochs_no_improve += 1
        if epochs_no_improve == patience:
            print("Early stopping triggered.")
            break

# Step 10: Load Best Model
model.load_state_dict(torch.load('best_han_bigru_model.pth'))

# Final evaluation
val_loss, val_preds, val_labels = eval_model(model, test_loader, criterion, device)
val_preds = (val_preds > 0.5).astype(int)
final_f1 = f1_score(val_labels, val_preds, average='weighted')
print(f"Final F1 Score: {final_f1:.4f}")


Loaded 400000 word vectors.
Epoch 1, Train Loss: 0.4501, Val Loss: 0.3535, Val F1 Score: 0.2668
Epoch 2, Train Loss: 0.3684, Val Loss: 0.3482, Val F1 Score: 0.3243
Epoch 3, Train Loss: 0.3619, Val Loss: 0.3427, Val F1 Score: 0.3550
Epoch 4, Train Loss: 0.3533, Val Loss: 0.3329, Val F1 Score: 0.3688
Epoch 5, Train Loss: 0.3416, Val Loss: 0.3236, Val F1 Score: 0.4362
Epoch 6, Train Loss: 0.3305, Val Loss: 0.3184, Val F1 Score: 0.4270
Epoch 7, Train Loss: 0.3215, Val Loss: 0.3108, Val F1 Score: 0.4706
Epoch 8, Train Loss: 0.3131, Val Loss: 0.3088, Val F1 Score: 0.4577
Epoch 9, Train Loss: 0.3103, Val Loss: 0.3071, Val F1 Score: 0.4695
Epoch 10, Train Loss: 0.3043, Val Loss: 0.3021, Val F1 Score: 0.5019
Epoch 11, Train Loss: 0.2985, Val Loss: 0.3005, Val F1 Score: 0.5081
Epoch 12, Train Loss: 0.2952, Val Loss: 0.2998, Val F1 Score: 0.5077
Epoch 13, Train Loss: 0.2919, Val Loss: 0.2976, Val F1 Score: 0.5250
Epoch 14, Train Loss: 0.2877, Val Loss: 0.2978, Val F1 Score: 0.5145
Epoch 15, Train

In [59]:
from sklearn.metrics import precision_score, recall_score, f1_score, accuracy_score
import numpy as np

# Function to tune threshold for each class
def tune_thresholds(model, dataloader, device, thresholds=None):
    model.eval()
    true_labels = []
    predicted_probs = []
    
    with torch.no_grad():
        for inputs, labels in dataloader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            predicted_probs.append(torch.sigmoid(outputs).cpu().numpy())
            true_labels.append(labels.cpu().numpy())
    
    predicted_probs = np.vstack(predicted_probs)
    true_labels = np.vstack(true_labels)
    
    # Tune thresholds if none are provided
    if thresholds is None:
        thresholds = np.linspace(0.1, 0.9, 9)  # Tune from 0.1 to 0.9
    
    best_thresholds = []
    for i in range(true_labels.shape[1]):  # For each label
        best_f1 = 0
        best_thresh = 0.5  # Default threshold is 0.5
        
        for thresh in thresholds:
            pred_labels = (predicted_probs[:, i] > thresh).astype(int)
            f1 = f1_score(true_labels[:, i], pred_labels)
            if f1 > best_f1:
                best_f1 = f1
                best_thresh = thresh
        
        best_thresholds.append(best_thresh)
        print(f"Best threshold for class {i}: {best_thresh}")
    
    return best_thresholds

# Tune thresholds on the validation/test set
best_thresholds = tune_thresholds(model, test_loader, device)

# Predict with tuned thresholds
def predict_with_tuned_thresholds(model, dataloader, device, thresholds):
    model.eval()
    all_preds = []
    all_true = []
    
    with torch.no_grad():
        for inputs, labels in dataloader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            probs = torch.sigmoid(outputs).cpu().numpy()
            preds = np.zeros_like(probs)
            
            # Apply custom thresholds
            for i, threshold in enumerate(thresholds):
                preds[:, i] = (probs[:, i] > threshold).astype(int)
            
            all_preds.append(preds)
            all_true.append(labels.cpu().numpy())
    
    all_preds = np.vstack(all_preds)
    all_true = np.vstack(all_true)
    
    return all_preds, all_true

# Get predictions with tuned thresholds
predicted_labels, true_labels = predict_with_tuned_thresholds(model, test_loader, device, best_thresholds)

# Calculate performance metrics with tuned thresholds
f1 = f1_score(true_labels, predicted_labels, average='weighted')
precision = precision_score(true_labels, predicted_labels, average='weighted')
recall = recall_score(true_labels, predicted_labels, average='weighted')
accuracy = accuracy_score(true_labels, predicted_labels)

print(f"Tuned Thresholds - F1 Score: {f1:.4f}, Precision: {precision:.4f}, Recall: {recall:.4f}, Accuracy: {accuracy:.4f}")


Best threshold for class 0: 0.30000000000000004
Best threshold for class 1: 0.5
Best threshold for class 2: 0.30000000000000004
Best threshold for class 3: 0.2
Best threshold for class 4: 0.2
Best threshold for class 5: 0.2
Best threshold for class 6: 0.2
Best threshold for class 7: 0.1
Best threshold for class 8: 0.2
Best threshold for class 9: 0.2
Best threshold for class 10: 0.2
Best threshold for class 11: 0.4
Best threshold for class 12: 0.2
Best threshold for class 13: 0.30000000000000004
Best threshold for class 14: 0.4
Best threshold for class 15: 0.4
Best threshold for class 16: 0.5
Best threshold for class 17: 0.2
Best threshold for class 18: 0.2
Best threshold for class 19: 0.30000000000000004
Best threshold for class 20: 0.1
Best threshold for class 21: 0.4
Best threshold for class 22: 0.2
Best threshold for class 23: 0.30000000000000004
Best threshold for class 24: 0.2
Best threshold for class 25: 0.30000000000000004
Best threshold for class 26: 0.1
Tuned Thresholds - F1 S

/software/slurm/spackages/linux-rocky8-x86_64/gcc-12.2.0/anaconda3-2023.09-0-3mhml42fa64byxqyd5fig5tbih625dp2/lib/python3.11/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [60]:
from sklearn.metrics import classification_report

# Print the classification report with tuned thresholds
report = classification_report(true_labels, predicted_labels, target_names=mlb.classes_, zero_division=1)
print(report)


                         precision    recall  f1-score   support

                              0.84      0.96      0.89       747
         ACKNOWLEDGMENT       1.00      0.00      0.00         6
                    ADD       0.50      0.43      0.46       138
         ASKING_DETAILS       0.39      0.57      0.47       109
                 CHANGE       0.38      0.48      0.43        84
                CONTENT       0.41      0.70      0.51       247
                CONTEXT       0.50      0.82      0.62       295
                 DELETE       0.27      0.40      0.32        30
             DISCUSSION       0.28      0.25      0.26        32
                   DONE       0.52      0.27      0.36        62
              EXECUTION       0.55      0.32      0.41        65
               EXPLICIT       0.66      0.67      0.66       248
               FEEDBACK       0.63      0.40      0.49        43
                 FORMAT       0.60      0.46      0.52        70
   INFORMATION EXCHANGE 

Chosen Model: Hierarchical Attention Network (HAN)
We chose the Hierarchical Attention Network (HAN) for text classification because it is well-suited for handling hierarchical structures in language, such as document-level classification, by focusing on both word-level and sentence-level representations. HAN is particularly good for capturing long-range dependencies in textual data, and it uses attention mechanisms to highlight the most important words and sentences for the task.
2. GloVe Embeddings: Pre-trained Word Representations
GloVe embeddings (Global Vectors for Word Representation) are used in this model as input embeddings because they capture the semantic meaning of words. GloVe is pre-trained on large corpora, which allows the model to leverage rich word semantics even with a smaller dataset. Using these embeddings improves the model's ability to generalize, especially in cases where specific word patterns are important for classification.
The embeddings are 300-dimensional, which is a high-dimensional vector space that captures more information about the words than lower-dimensional spaces

Model Architecture: BiGRU + Attention (HAN)
The HAN model consists of two main components:
Word-level BiGRU: The model starts with a Bidirectional GRU that processes word-level embeddings to capture contextual information in both directions (past and future).
Word-level Attention: An attention mechanism identifies the most relevant words in the sentence, giving more weight to important words.
Sentence-level BiGRU: Next, the output from the word-level GRU is processed by another BiGRU at the sentence level, capturing dependencies across sentences.
Sentence-level Attention: Again, an attention mechanism identifies important sentences in the document, helping the model focus on key parts of the text.
Layer Normalization: We introduced Layer Normalization to stabilize and accelerate training by normalizing the inputs across features.
raining Setup
The model was trained using Binary Cross-Entropy with Logits Loss (BCEWithLogitsLoss) because this is a multi-label classification task, where each comment can belong to multiple categories.
We used the AdamW optimizer (an improved version of Adam) to optimize the model's weights.
A OneCycleLR scheduler was used to adjust the learning rate dynamically, improving training efficiency.
Gradient Clipping was applied during training to prevent exploding gradients, which can destabilize the model.
Threshold Tuning
By default, classification models use a threshold of 0.5 for binary decisions. However, we performed threshold tuning for each class. This involves adjusting the threshold for each label (ranging from 0.1 to 0.9) to optimize the F1 score. The goal is to find the best threshold for each label to improve classification performance.
This tuning ensures that we maximize precision and recall based on the specific characteristics of each label.

Why We Used HAN + GloVe Embeddings
HAN is ideal for hierarchical text data, which suits this task of multi-level and multi-label classification, where comments are classified into different levels of categories.
GloVe embeddings allow the model to use pre-trained knowledge of word semantics, improving performance with fewer data and helping capture word relationships that are essential for classification tasks.
Summary of Results
After tuning the thresholds and training the model with attention, GRUs, and GloVe embeddings, the model showed promising results, improving its F1 score, precision, and recall across multiple levels.

In [72]:
import torch
import torch.nn as nn
import pandas as pd
import numpy as np
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.model_selection import train_test_split
from torch.utils.data import DataLoader, Dataset
from sklearn.metrics import f1_score, classification_report, precision_score, recall_score, accuracy_score
from torch.optim.lr_scheduler import OneCycleLR

# Step 1: Load Pre-trained GloVe embeddings
def load_glove_embeddings(glove_file, embedding_dim=300):
    embeddings_index = {}
    with open(glove_file, 'r', encoding='utf-8') as f:
        for line in f:
            values = line.split()
            word = values[0]
            coefs = np.asarray(values[1:], dtype='float32')
            embeddings_index[word] = coefs
    print(f'Loaded {len(embeddings_index)} word vectors.')
    return embeddings_index

# Load the GloVe embeddings
embedding_dim = 300
glove_file = 'glove.6B.300d.txt'  # Ensure this file is in your working directory
glove_embeddings = load_glove_embeddings(glove_file, embedding_dim)

# Step 2: Data Preparation
df = pd.read_csv('labeled_comments_cleaned.csv')
df.fillna('', inplace=True)

# Combine all label columns into a list of labels per row
df['combined_labels'] = df[['level_0', 'level_1', 'level_2', 'level_3', 'level_4']].values.tolist()

# Selecting the feature variable
X = df['comment_full_text']

# Split the dataset into training and testing sets
X_train, X_test = train_test_split(X, test_size=0.2, random_state=42)

# Step 3: Dataset Class (Zero-shot learning only needs text data)
class CommentsDataset(Dataset):
    def __init__(self, texts, glove_embeddings, embedding_dim=300, max_len=128):
        self.texts = texts.reset_index(drop=True)
        self.glove_embeddings = glove_embeddings
        self.embedding_dim = embedding_dim
        self.max_len = max_len

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        tokenized_text = text.split()[:self.max_len]
        
        # Convert words to GloVe embeddings, pad with zeros if shorter than max_len
        embedding_matrix = np.zeros((self.max_len, self.embedding_dim))
        for i, word in enumerate(tokenized_text):
            embedding_matrix[i] = self.glove_embeddings.get(word, np.zeros(self.embedding_dim))
        
        input_tensor = torch.tensor(embedding_matrix, dtype=torch.float32)
        return input_tensor

# Step 4: Create dataset and dataloaders (no labels needed for zero-shot)
test_dataset = CommentsDataset(X_test, glove_embeddings, embedding_dim=embedding_dim)
test_loader = DataLoader(test_dataset, batch_size=64)

# Step 5: Define CNN+BiGRU Hybrid Model
class CNN_BiGRU_Hybrid(nn.Module):
    def __init__(self, embedding_dim=300, hidden_size=256, dropout_prob=0.5):
        super(CNN_BiGRU_Hybrid, self).__init__()
        
        # CNN layers to capture local features
        self.conv1 = nn.Conv1d(embedding_dim, 128, kernel_size=3, padding=1)
        self.conv2 = nn.Conv1d(128, 128, kernel_size=3, padding=1)
        
        # BiGRU to capture long-range dependencies
        self.bigru = nn.GRU(128, hidden_size, bidirectional=True, batch_first=True)
        
        # Fully connected layer to project to 300-dimensional space
        self.fc = nn.Linear(hidden_size * 2, embedding_dim)  # Project to 300-dimensional GloVe space
        
        self.dropout = nn.Dropout(dropout_prob)
    
    def forward(self, inputs):
        # CNN layers (apply along the word embeddings)
        x = inputs.permute(0, 2, 1)  # Change shape to (batch_size, embedding_dim, max_len)
        x = torch.relu(self.conv1(x))
        x = torch.relu(self.conv2(x))
        
        # BiGRU
        x = x.permute(0, 2, 1)  # Change shape back to (batch_size, max_len, feature_dim)
        x, _ = self.bigru(x)
        
        # Fully connected layer
        x = self.fc(self.dropout(x[:, -1, :]))  # Take the last time-step output for classification
        
        return x

# Step 6: Initialize Model
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = CNN_BiGRU_Hybrid(hidden_size=256, embedding_dim=embedding_dim).to(device)

# Step 7: Predict using the trained model and GloVe embeddings
def get_cnn_bigru_embeddings(model, dataloader, device):
    model.eval()
    embeddings = []
    with torch.no_grad():
        for inputs in dataloader:
            inputs = inputs.to(device)
            output = model(inputs)
            embeddings.append(output.cpu().numpy())
    return np.vstack(embeddings)

def get_label_glove_embeddings(labels, glove_embeddings):
    return np.array([glove_embeddings.get(label.lower(), np.zeros(300)) for label in labels])

def calculate_similarity(comment_embeddings, label_embeddings):
    # Normalize the embeddings
    normalized_comment_embeddings = comment_embeddings / np.linalg.norm(comment_embeddings, axis=1, keepdims=True)
    normalized_label_embeddings = label_embeddings / np.linalg.norm(label_embeddings, axis=1, keepdims=True)
    # Calculate cosine similarity
    similarities = np.dot(normalized_comment_embeddings, normalized_label_embeddings.T)
    return similarities

def predict_labels_cnn_bigru(model, dataloader, label_embeddings, candidate_labels, device):
    # Get comment embeddings
    comment_embeddings = get_cnn_bigru_embeddings(model, dataloader, device)
    
    # Calculate similarity between comment embeddings and label embeddings
    similarities = calculate_similarity(comment_embeddings, label_embeddings)
    
    # Choose the most similar label based on cosine similarity
    predicted_label_ids = np.argmax(similarities, axis=1)
    predicted_labels = [candidate_labels[label_id] for label_id in predicted_label_ids]
    
    return predicted_labels

def evaluate_for_level_cnn_bigru(model, level_name, candidate_labels, glove_embeddings, device):
    print(f"\nEvaluating for {level_name}...")

    X_test = df['comment_full_text']
    y_test = df[level_name].tolist()

    X_test, y_test = zip(*[(comment, label) for comment, label in zip(X_test, y_test) if label])

    dataset = CommentsDataset(pd.Series(X_test), glove_embeddings)
    test_loader = DataLoader(dataset, batch_size=64, shuffle=False)

    label_embeddings = get_label_glove_embeddings(candidate_labels, glove_embeddings)

    # Predict labels with CNN+BiGRU Hybrid
    predicted_labels = predict_labels_cnn_bigru(model, test_loader, label_embeddings, candidate_labels, device)

    # Normalize the labels for comparison
    y_test = [label.lower() for label in y_test]
    predicted_labels = [label.lower() for label in predicted_labels]

    # Calculate metrics
    print("Calculating metrics...")
    f1 = f1_score(y_test, predicted_labels, average='weighted', zero_division=1)
    precision = precision_score(y_test, predicted_labels, average='weighted', zero_division=1)
    recall = recall_score(y_test, predicted_labels, average='weighted', zero_division=1)
    accuracy = accuracy_score(y_test, predicted_labels)
    report = classification_report(y_test, predicted_labels, zero_division=1)

    print(f"F1 Score for {level_name}: {f1}")
    print(f"Precision for {level_name}: {precision}")
    print(f"Recall for {level_name}: {recall}")
    print(f"Accuracy for {level_name}: {accuracy}")
    print(f"Classification Report for {level_name}:\n", report)

# Define level categories for each level
level_categories = {
    'level_0': ['INFORMATION EXCHANGE', 'MODIFICATION', 'SOCIAL COMMUNICATION', 'OTHER'],
    'level_1': ['REQUESTED', 'EXECUTION', 'DISCUSSION', 'PROVIDED', 'FEEDBACK', 'ACKNOWLEDGMENT'],
    'level_2': ['REQUESTING_CONFIRMATION', 'PROMISE', 'CONTENT', 'REFERENCE', 'CONTEXT', 'THREAD', 'DONE', 'FORMAT', 'ASKING_DETAILS'],
    'level_3': ['POTENTIAL_CHANGE', 'NOT_POTENTIAL_CHANGE', 'EXPLICIT', 'NOT_EXPLICIT'],
    'level_4': ['CHANGE', 'ADD', 'DELETE']
}

# Evaluate for all levels using CNN+BiGRU Hybrid
for level_name, candidate_labels in level_categories.items():
    evaluate_for_level_cnn_bigru(model, level_name, candidate_labels, glove_embeddings, device)


Loaded 400000 word vectors.

Evaluating for level_0...


/local_scratch/slurm.734766/ipykernel_305734/731169658.py:121: RuntimeWarning: invalid value encountered in divide
  normalized_label_embeddings = label_embeddings / np.linalg.norm(label_embeddings, axis=1, keepdims=True)


Calculating metrics...
F1 Score for level_0: 0.33055426982912295
Precision for level_0: 0.7500062725608961
Recall for level_0: 0.4974954918853937
Accuracy for level_0: 0.4974954918853937
Classification Report for level_0:
                       precision    recall  f1-score   support

information exchange       0.50      1.00      0.66      2483
        modification       1.00      0.00      0.00      1886
               other       1.00      0.00      0.00       273
social communication       1.00      0.00      0.00       349

            accuracy                           0.50      4991
           macro avg       0.87      0.25      0.17      4991
        weighted avg       0.75      0.50      0.33      4991


Evaluating for level_1...
Calculating metrics...
F1 Score for level_1: 0.001882885383088188
Precision for level_1: 0.9698135054460284
Recall for level_1: 0.03115727002967359
Accuracy for level_1: 0.03115727002967359
Classification Report for level_1:
                 precision

/local_scratch/slurm.734766/ipykernel_305734/731169658.py:121: RuntimeWarning: invalid value encountered in divide
  normalized_label_embeddings = label_embeddings / np.linalg.norm(label_embeddings, axis=1, keepdims=True)


Calculating metrics...
F1 Score for level_2: 0.001855150387181577
Precision for level_2: 0.9700328211741988
Recall for level_2: 0.0309234378332267
Accuracy for level_2: 0.0309234378332267
Classification Report for level_2:
                          precision    recall  f1-score   support

         asking_details       1.00      0.00      0.00       553
                content       1.00      0.00      0.00      1384
                context       1.00      0.00      0.00      1425
                   done       1.00      0.00      0.00       253
                 format       1.00      0.00      0.00       405
                promise       1.00      0.00      0.00        17
              reference       1.00      0.00      0.00       358
requesting_confirmation       0.03      1.00      0.06       145
                 thread       1.00      0.00      0.00       149

               accuracy                           0.03      4689
              macro avg       0.89      0.11      0.01     

/local_scratch/slurm.734766/ipykernel_305734/731169658.py:121: RuntimeWarning: invalid value encountered in divide
  normalized_label_embeddings = label_embeddings / np.linalg.norm(label_embeddings, axis=1, keepdims=True)


Calculating metrics...
F1 Score for level_3: 0.2478300176650666
Precision for level_3: 0.7564989301092208
Recall for level_3: 0.41938405797101447
Accuracy for level_3: 0.41938405797101447
Classification Report for level_3:
                       precision    recall  f1-score   support

            explicit       1.00      0.00      0.00      1504
        not_explicit       1.00      0.00      0.00        83
not_potential_change       1.00      0.00      0.00       977
    potential_change       0.42      1.00      0.59      1852

            accuracy                           0.42      4416
           macro avg       0.85      0.25      0.15      4416
        weighted avg       0.76      0.42      0.25      4416


Evaluating for level_4...
Calculating metrics...
F1 Score for level_4: 0.3099811007934938
Precision for level_4: 0.6548335980289898
Recall for level_4: 0.3613500992720053
Accuracy for level_4: 0.3613500992720053
Classification Report for level_4:
               precision    r

1. Zero-Shot Learning with HAN: What It Would Involve
Zero-shot learning is typically done with models that are pre-trained on diverse, large-scale datasets and are capable of handling tasks they have never been explicitly trained for. HAN (Hierarchical Attention Network), however, is not designed for zero-shot learning in the traditional sense. Instead, it is a supervised learning model meant to be trained on a specific dataset for a specific task.

In the context of zero-shot learning with HAN, the model would attempt to classify unseen data without task-specific training. Here’s how zero-shot with HAN would work:

Embedding Representations: Instead of training HAN on the dataset, I could use pre-trained GloVe embeddings to represent both the input comments and the labels. These embeddings capture the semantic meaning of words, which allows the model to reason about unseen data based on the relationships between the words in the input and the label descriptions.
Cosine Similarity for Classification: After generating embeddings for both the input comments and the possible labels, I would use cosine similarity to measure how similar the embeddings are. The label with the highest similarity to the input comment would be chosen as the predicted label.
This would allow HAN to perform a form of zero-shot classification, even though it is not traditionally built for this. By leveraging the pre-trained GloVe embeddings, HAN can approximate zero-shot learning by comparing the semantic similarity between comments and the labels' representations.

2. Challenges of Using HAN for Zero-Shot Learning
Not Pre-Trained for Zero-Shot Tasks: Unlike models like BERT, RoBERTa, or Gemini, HAN was not pre-trained on diverse datasets for general-purpose learning. It is instead trained on a specific task (like document classification or multi-label classification) using labeled data. Therefore, HAN lacks the generalization abilities that zero-shot models inherently have.
Supervised Learning Structure: HAN relies on a hierarchical structure (word-level and sentence-level GRU with attention) and requires labeled data to learn these hierarchies effectively. Using it for zero-shot without training would mean that it is not benefiting from its hierarchical structure, as no training would be done to learn the task-specific hierarchies.
3. Main Work of HAN
The main function of the Hierarchical Attention Network (HAN) is to classify textual data by focusing on both word-level and sentence-level structures. Its core components include:

Word-Level GRU and Attention: This part of HAN focuses on capturing the contextual relationships between words in a sentence. By using a Bidirectional GRU, it captures dependencies from both past and future contexts. The attention mechanism then identifies the most important words in the sentence for the classification task.

Sentence-Level GRU and Attention: Once the word-level attention is applied, the sentence representations are processed using another Bidirectional GRU to capture relationships between sentences. The sentence-level attention highlights the most important sentences in the document, ensuring that the model focuses on the key parts of the text.

Hierarchical Structure: The hierarchical nature of HAN (word-level and sentence-level attention) allows it to handle longer documents or more complex inputs that span multiple sentences or paragraphs. This makes HAN ideal for tasks like document classification, where both word and sentence information are crucial for understanding the overall meaning.

Supervised Learning: HAN is typically trained on labeled datasets, meaning it requires supervision in the form of labels to learn how to perform its classification task. The model is fine-tuned to a specific task using this training data.

4. Why HAN Was Not Used for True Zero-Shot Learning
In summary, HAN was not used for zero-shot learning because it is inherently a supervised learning model. It was designed to be trained on task-specific data, unlike zero-shot models like BERT or RoBERTa, which can generalize to new tasks without needing fine-tuning. While HAN can attempt to perform zero-shot tasks using embeddings and cosine similarity, it lacks the generalization and flexibility that zero-shot models are built for.

Training hcapsnet model 